# imports

In [1]:
from os import listdir,mkdir,makedirs
from os.path import isfile, join, isdir,exists
import pandas as pd
import numpy as np
from scipy import stats
import re


import matplotlib.pyplot as plt
from matplotlib.backends.backend_pdf import PdfPages
from myplots import roundup, rounddown, find_decimal_fold, percentile_cut_off, rarefaction_calc, rarefaction_plot,draw_correlation_scatter
from matplotlib.ticker import FormatStrFormatter
import cPickle as pickle
from Bio.SeqUtils import GC
import seaborn as sns
import random
from scipy.stats import pearsonr,fisher_exact
from skbio.diversity.alpha import shannon, simpson, berger_parker_d

from pop_organize import get_sample_data, get_sample_with_dfs
from SufficientStatistics import *
from MyFunctionsShani import *
import math
from myplots import roundup, rounddown, find_decimal_fold
from skbio.stats.distance import mantel
from scipy.spatial.distance import braycurtis, pdist, euclidean


from GeneralFeaturePhenotypeInteractions.Feature_phenotype_functions import * 
from TCR_microbiome_interactions.TCR_microbiome_interactions_functions import *
from TCR_microbiome_interactions.TCR_microbiome_interactions_functions2 import *
from SampleLists.SampleFileFunctions import *
from PhenotypicData.PhenotypeGenerationFunctions import *
from CardioProject.CardioFunctions import *
from PredictionPipeline.PredictionFunctions import *
from TCR_feature_generation.SubsamplingFunctions import *

import os
from Utils import cacheOnDisk
from queue.qp import qp,fakeqp
from addloglevels import sethandlers

#ML imports:
from xgboost import XGBClassifier,XGBRegressor
import lightgbm as lgb
from collections import OrderedDict
from sklearn.model_selection import GroupKFold,StratifiedKFold, KFold
import statsmodels.formula.api as sm
from sklearn.linear_model import LogisticRegression
import shap
from sklearn import metrics, preprocessing
from sklearn.svm import LinearSVC
from sklearn.feature_selection import SelectFromModel,SelectKBest,chi2,mutual_info_classif,f_classif,f_regression
from sklearn.naive_bayes import GaussianNB

MyPath='/net/mraid08/export/genie/Lab/Personal/ShaniBAF'
posterFolder='%s/Presentations and Manuscripts/ImmunoRepertoire conference - Paris2018/Poster/new' %MyPath

with open('/net/mraid08/export/genie/Lab/Personal/ShaniBAF/Sample files/BD lists/PNP530','rb') as fp:
    PNP530=pickle.load(fp)
with open('/net/mraid08/export/genie/Lab/Personal/ShaniBAF/Sample files/BD lists/Cardio126','rb') as fp:
    Cardio126=pickle.load(fp)
PNP530Cardio126=PNP530+Cardio126

done1
stop
stop
done1
stop
done
done
done
done


'24102018'

## get TCRdf tables (1,5,10) and BD-FD converter table:

In [ ]:
BDFDfile='%s/Sample files/updatedBDandFDlists/BDfile_31052018.xlsx' %MyPath
BDFD=pd.read_excel(BDFDfile).set_index('DnaID')[['UserID','corrected_regCode','Blood_Date']]
BDFD.index=BDFD.index.rename('BD')

with open('/net/mraid08/export/genie/Lab/Personal/ShaniBAF/Sample files/BD lists/PNP530','rb') as fp:
    PNP530=pickle.load(fp)
with open('/net/mraid08/export/genie/Lab/Personal/ShaniBAF/Sample files/BD lists/Cardio126','rb') as fp:
    Cardio126=pickle.load(fp)
PNP530Cardio126list=PNP530+Cardio126

BDFD=BDFD.loc[PNP530Cardio126list,:]
BDFD.head()

In [ ]:
duplicates=BDFD.duplicated(subset='UserID',keep=False)
BDFD[duplicates]

In [ ]:
folder='%s/TCR_real_data/sharingAnalysis' %MyPath

fileList=['sharingMatrix_PNP530_minNshared2_RA_onlyProductiveTrue__percShared5_OLtrimmed_binary',
         'sharingMatrix_PNP530_minNshared2_RA_onlyProductiveTrue__percShared10_OLtrimmed_binary']

for f in fileList:
    f1='%s/%s' %(folder,f)
    df=pd.read_pickle(f1)
    try:
        df=df.set_index('BD')
    except:
        print 'index is already BD'
        
    merged=pd.merge(df,BDFD,how='inner',left_index=True,right_index=True)
    print f
    print merged.shape
    print merged.iloc[:4,:4]
    
    newFile='%s/%s_withInfo' %(folder,f)
    merged.to_pickle(newFile)
    

# use Noam's prediction code to predict metabolites:

## convert metabolite table to be indexed by BD:

In [10]:
#BDFD converter
BDFDfile='%s/Sample files/updatedBDandFDlists/final_BD_FD_converter_mergedOnDate_RCfolderAllSeqProjects_31052018.xlsx' %MyPath
BDFD=pd.read_excel(BDFDfile)[['BD','FD']]
BDFD.head()

#sample lists:
with open('/net/mraid08/export/genie/Lab/Personal/ShaniBAF/Sample files/BD lists/PNP530','rb') as fp:
    PNP530=pickle.load(fp)
with open('/net/mraid08/export/genie/Lab/Personal/ShaniBAF/Sample files/BD lists/Cardio126','rb') as fp:
    Cardio126=pickle.load(fp)
PNP530Cardio126list=PNP530+Cardio126


data_list=['tmao','acs_top20']


for data in data_list:
    print data
    f1='%s/TCR_real_data/metabolomics/%s.csv' %(MyPath,data)
    df=pd.read_csv(f1)
    df['FD']=df['FD_SPID'].str.split('_')
    df['FD']=df['FD_SPID'].apply(lambda x: x.split('_')[0])
    print ('FD value counts:',df['FD'].value_counts().sort_values(ascending=False).head())

    df_BD=pd.merge(df,pd.DataFrame(BDFD), how='inner',left_on='FD',right_on='FD')
    print ('BD value counts:',df_BD['BD'].value_counts().sort_values(ascending=False).head())
    
    df_BD=df_BD.set_index('BD')
    df_BD=df_BD.loc[PNP530,:]
    df_BD=df_BD.dropna(how='all')
    
    df_BD['ind']=df_BD.index.str.replace('BD','').astype(int)
    # df_BD['ind'].sort_values(ascending=False)

    df_BD['isCardio']=np.where(df_BD['ind']>949,1,0)
    print ('how many cardio:', df_BD['isCardio'].value_counts(dropna=False))

    df_BD=df_BD.drop(['FD','FD_SPID','ind','isCardio'],axis=1)
    
    
    print ('final df head:', df_BD.head())
    print ('final df shape:',df_BD.shape)
    
    f2='%s/TCR_real_data/metabolomics/%s_BD_PNP530.dat' %(MyPath,data)
    df_BD.to_pickle(f2)
    
    print 'done saving'



tmao
('FD value counts:', FD2524    1
FD160     1
FD174     1
FD471     1
FD476     1
Name: FD, dtype: int64)
('BD value counts:', BD670    1
BD376    1
BD673    1
BD674    1
BD675    1
Name: BD, dtype: int64)
('how many cardio:', 0    270
Name: isCardio, dtype: int64)
('final df head:',        100003397
BD              
BD406   7.529393
BD228   7.948972
BD714   8.322199
BD617   7.658798
BD143   7.841049)
('final df shape:', (270, 1))
done saving
acs_top20
('FD value counts:', FD2524    1
FD160     1
FD174     1
FD471     1
FD476     1
Name: FD, dtype: int64)
('BD value counts:', BD670    1
BD376    1
BD673    1
BD674    1
BD675    1
Name: BD, dtype: int64)
('how many cardio:', 0    270
Name: isCardio, dtype: int64)
('final df head:',        100001271  100001272  100001395  100008929  100000008  100001409  \
BD                                                                        
BD406   8.544265   8.445331   8.738178   5.754502   6.512221   6.029122   
BD228   8.609368   8.360634   

In [ ]:
df_BD['ind']=df_BD.index.str.replace('BD','').astype(int)
# df_BD['ind'].sort_values(ascending=False)

df_BD['isCardio']=np.where(df_BD['ind']>949,1,0)
df_BD['isCardio'].value_counts(dropna=False)

## run Noam's prediction module for TMAO

### using corrected features with rels, not including TCR sequences

In [12]:
!python /home/sbenari/workspace/Microbiome/ShaniBA/RandomizedSearchCV_SHAP_LGBM_Shani.py /net/mraid08/export/\
genie/Lab/Personal/ShaniBAF/TCR_real_data/metabolomics/predictions_NoamMod/TMAO_nrandom20/ -path_to_X\
 /net/mraid08/export/genie/Lab/Personal/ShaniBAF/TCR_real_data/Predictions/featureDFs/allTCRfeatures_percShared10__withRels_AgeGenderGFRCorr.dat\
 -path_to_Y /net/mraid08/export/genie/Lab/Personal/ShaniBAF/TCR_real_data/metabolomics/tmao_BD_PNP530.dat\
 -n_random 20

/usr/wisdom/python/lib/python2.7/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
main
upload_these_jobs
/home/sbenari/workspace/lib/queue/qp.py:666: FutureWarning: 'argmin' is deprecated, use 'idxmin' instead. The behavior of 'argmin'
will be corrected to return the positional minimum in the future.
Use 'series.values.argmin' to get the position of the minimum now.
  ans = a[a.index.isin(comp[comp].index) | (a.index == user)].argmin() == user
2018-10-24 15:31:42,125 - qp - INFO - Sending to queue (mem 2G, threads 2): python2.7 -W ignore /home/sbenari/workspace/lib/queue/qworker.py SHAP-RSCV_9ae9ff5c57984dc4a077a4d7a5214e33/0.dat;
2018-10-24 15:52:45,267 - qp - INFO - 
	python2.7 -W ignore /home/sbenari/workspace/lib/queue/qworker.py SHAP-RSCV_9ae9ff5c57984dc4

	[LightGBM] [Warning] min_data_in_leaf is set=26, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=26.
	[LightGBM] [Warning] num_threads is set=1, nthread=-1 will be ignored. Current value: num_threads=1.
	[LightGBM] [Warning] bagging_fraction is set=0.7, subsample=1.0 will be ignored. Current value: bagging_fraction=0.7.
	[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9.
	[LightGBM] [Warning] bagging_freq is set=3, subsample_freq=1 will be ignored. Current value: bagging_freq=3.
	[LightGBM] [Warning] min_data_in_leaf is set=26, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=26.
	[LightGBM] [Warning] num_threads is set=1, nthread=-1 will be ignored. Current value: num_threads=1.
	[LightGBM] [Warning] bagging_fraction is set=0.7, subsample=1.0 will be ignored. Current value: bagging_fraction=0.7.
	[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 wi

concat_outputs


In [13]:
f1='%s/TCR_real_data/metabolomics/predictions_NoamMod/TMAO_nrandom20/results_df.pkl' %MyPath
results_df=pd.read_pickle(f1)
results_df

Size Coefficient_of_determination  pearson_r pearson_p spearman_r  \
100003397  270                   -0.0302049 -0.0731759  0.230749 -0.0339002   

          spearman_p  
100003397    0.57916

### using TCR sequences

In [24]:
!python /home/sbenari/workspace/Microbiome/ShaniBA/RandomizedSearchCV_SHAP_LGBM_Shani.py /net/mraid08/export/\
genie/Lab/Personal/ShaniBAF/TCR_real_data/metabolomics/predictions_NoamMod/TMAO_bySeqs_nrandom20/ -path_to_X\
 /net/mraid08/export/genie/Lab/Personal/ShaniBAF/TCR_real_data/sharingAnalysis/sharingMatrix_PNP530_minNshared2_RA_onlyProductiveTrue__percShared5_OLtrimmed_binary\
 -path_to_Y /net/mraid08/export/genie/Lab/Personal/ShaniBAF/TCR_real_data/metabolomics/tmao_BD_PNP530Cardio126.dat\
 -n_random 20

/usr/wisdom/python/lib/python2.7/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
main
upload_these_jobs
2018-10-25 13:50:22,513 - qp - INFO - Sending to queue (mem 2G, threads 2): python2.7 -W ignore /home/sbenari/workspace/lib/queue/qworker.py SHAP-RSCV_817542c8805243e3a50dcc43afe9be4c/0.dat;
/home/sbenari/workspace/lib/queue/qp.py:666: FutureWarning: 'argmin' is deprecated, use 'idxmin' instead. The behavior of 'argmin'
will be corrected to return the positional minimum in the future.
Use 'series.values.argmin' to get the position of the minimum now.
  ans = a[a.index.isin(comp[comp].index) | (a.index == user)].argmin() == user
2018-10-25 15:43:26,061 - qp - INFO - 
	python2.7 -W ignore /home/sbenari/workspace/lib/queue/qworker.py SHAP-RSCV_817542c8805243e3

	[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8.
	[LightGBM] [Warning] feature_fraction is set=0.8, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8.
	[LightGBM] [Warning] bagging_freq is set=2, subsample_freq=1 will be ignored. Current value: bagging_freq=2.
	[LightGBM] [Warning] min_data_in_leaf is set=31, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=31.
	[LightGBM] [Warning] num_threads is set=1, nthread=-1 will be ignored. Current value: num_threads=1.
	[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8.
	[LightGBM] [Warning] feature_fraction is set=0.8, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8.
	[LightGBM] [Warning] bagging_freq is set=2, subsample_freq=1 will be ignored. Current value: bagging_freq=2.
	[LightGBM] [Warning] min_data_in_leaf is set=31, min_child_samp

concat_outputs


In [ ]:
f1='%s/TCR_real_data/metabolomics/predictions_NoamMod/TMAO_bySeqs_nrandom20/results_df.pkl' %MyPath
results_df=pd.read_pickle(f1)
results_df

In [19]:
f1='%s/TCR_real_data/metabolomics/predictions_NoamMod/TMAO_bySeqs_nrandom20/results_df.pkl' %MyPath
results_df=pd.read_pickle(f1)
results_df.sort_values(by='pearson_r',ascending=False)

Size Coefficient_of_determination  pearson_r    pearson_p  \
100001777  270                    0.0356276   0.203962  0.000747871   
100001322  179                   0.00642244  0.0858936     0.252939   
100015966  270                  -0.00335432  0.0841626     0.167906   
100003588  231                   -0.0155503  0.0487083      0.46129   
1094       270                  -0.00795171  0.0463861     0.447808   
100001271  270                  7.05509e-05  0.0454214     0.457318   
100020908  270                   -0.0172872  0.0281564     0.645084   
100001126  268                   -0.0108014  0.0132527     0.829025   
1504       270                   -0.0157045 -0.0193874     0.751154   
100001272  270                  -0.00574098  -0.024041     0.694129   
100008929  268                   -0.0148422 -0.0272007     0.657553   
100000008  270                  -0.00809257 -0.0372363     0.542373   
X - 24549  270                  -0.00485274 -0.0550226       0.3678   
100001806  247                   -0.0465828 -0.0568843     0.373362   
X - 21411  266                     -0.04465 -0.0772514     0.209161   
100001263  270                   -0.0249865 -0.0835984     0.170785   
100015759  270                   -0.0192912  -0.120535    0.0478577   
100001395  270                  -0.00976721   -0.13974    0.0216307   
X - 24473  259                   -0.0227931  -0.181826   0.00331855   
100001409  270                   -0.0175649  -0.206934  0.000622507   

           spearman_r  spearman_p  
100001777    0.180174  0.00296662  
100001322   0.0531727    0.479617  
100015966   0.0685923    0.261361  
100003588   0.0324091    0.624111  
1094        0.0407547    0.504875  
100001271   0.0363242    0.552315  
100020908   0.0903402    0.138718  
100001126   0.0432817    0.480455  
1504       0.00860684    0.888051  
100001272  -0.0105343    0.863204  
100008929  -0.0553603    0.366662  
100000008  -0.0752597    0.217705  
X - 24549  -0.0850955    0.163226  
100001806  -0.0282861    0.658211  
X - 21411  -0.0763025    0.214826  
100001263  -0.0445543    0.465961  
100015759  -0.0830446    0.173646  
100001395    -0.16189  0.00768987  
X - 24473   -0.168389  0.00660212  
100001409    -0.12643   0.0378801

## run Noam's prediction module for top20 metabolites

### using corrected features:

In [14]:
!python /home/sbenari/workspace/Microbiome/ShaniBA/RandomizedSearchCV_SHAP_LGBM_Shani.py /net/mraid08/export/\
genie/Lab/Personal/ShaniBAF/TCR_real_data/metabolomics/predictions_NoamMod/top20_nrandom20/ -path_to_X\
 /net/mraid08/export/genie/Lab/Personal/ShaniBAF/TCR_real_data/Predictions/featureDFs/allTCRfeatures_percShared10__withRels_AgeGenderGFRCorr.dat\
 -path_to_Y /net/mraid08/export/genie/Lab/Personal/ShaniBAF/TCR_real_data/metabolomics/acs_top20_BD_PNP530.dat\
 -n_random 20

/usr/wisdom/python/lib/python2.7/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
main
upload_these_jobs
/home/sbenari/workspace/lib/queue/qp.py:666: FutureWarning: 'argmin' is deprecated, use 'idxmin' instead. The behavior of 'argmin'
will be corrected to return the positional minimum in the future.
Use 'series.values.argmin' to get the position of the minimum now.
  ans = a[a.index.isin(comp[comp].index) | (a.index == user)].argmin() == user
2018-10-24 16:19:37,816 - qp - INFO - Sending to queue (mem 2G, threads 2): python2.7 -W ignore /home/sbenari/workspace/lib/queue/qworker.py SHAP-RSCV_c061f220735f4ff5988ceb631a30a18b/0.dat;
2018-10-24 16:19:52,662 - qp - INFO - Sending to queue (mem 2G, threads 2): python2.7 -W ignore /home/sbenari/workspace/lib/queue/q

	[LightGBM] [Warning] bagging_fraction is set=0.6, subsample=1.0 will be ignored. Current value: bagging_fraction=0.6.
	[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6.
	[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=1 will be ignored. Current value: bagging_freq=1.
	[LightGBM] [Warning] min_data_in_leaf is set=16, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=16.
	[LightGBM] [Warning] num_threads is set=1, nthread=-1 will be ignored. Current value: num_threads=1.
	[LightGBM] [Warning] bagging_fraction is set=0.6, subsample=1.0 will be ignored. Current value: bagging_fraction=0.6.
	[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6.
	[LightGBM] [Warning] bagging_freq is set=0, subsample_freq=1 will be ignored. Current value: bagging_freq=0.
	[LightGBM] [Warning] min_data_in_leaf is set=1, min_child_sampl

	[LightGBM] [Warning] num_threads is set=1, nthread=-1 will be ignored. Current value: num_threads=1.
	[LightGBM] [Warning] bagging_fraction is set=0.7, subsample=1.0 will be ignored. Current value: bagging_fraction=0.7.
	[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9.
	[LightGBM] [Warning] bagging_freq is set=0, subsample_freq=1 will be ignored. Current value: bagging_freq=0.
	[LightGBM] [Warning] min_data_in_leaf is set=26, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=26.
	[LightGBM] [Warning] num_threads is set=1, nthread=-1 will be ignored. Current value: num_threads=1.
	[LightGBM] [Warning] bagging_fraction is set=0.7, subsample=1.0 will be ignored. Current value: bagging_fraction=0.7.
	[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9.
	[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=1 will be ig

	[LightGBM] [Warning] bagging_freq is set=0, subsample_freq=1 will be ignored. Current value: bagging_freq=0.
	[LightGBM] [Warning] min_data_in_leaf is set=21, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=21.
	[LightGBM] [Warning] num_threads is set=1, nthread=-1 will be ignored. Current value: num_threads=1.
	[LightGBM] [Warning] bagging_fraction is set=0.9, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9.
	[LightGBM] [Warning] feature_fraction is set=0.5, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.5.
	[LightGBM] [Warning] bagging_freq is set=0, subsample_freq=1 will be ignored. Current value: bagging_freq=0.
	[LightGBM] [Warning] min_data_in_leaf is set=21, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=21.
	[LightGBM] [Warning] num_threads is set=1, nthread=-1 will be ignored. Current value: num_threads=1.
	[LightGBM] [Warning] bagging_fraction is set=0.9, subsample=1.0 will be ignored. C

	[LightGBM] [Warning] num_threads is set=1, nthread=-1 will be ignored. Current value: num_threads=1.
	[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8.
	[LightGBM] [Warning] feature_fraction is set=0.4, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.4.
	[LightGBM] [Warning] bagging_freq is set=5, subsample_freq=1 will be ignored. Current value: bagging_freq=5.
	[LightGBM] [Warning] min_data_in_leaf is set=16, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=16.
	[LightGBM] [Warning] num_threads is set=1, nthread=-1 will be ignored. Current value: num_threads=1.
	[LightGBM] [Warning] bagging_fraction is set=0.7, subsample=1.0 will be ignored. Current value: bagging_fraction=0.7.
	[LightGBM] [Warning] feature_fraction is set=0.4, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.4.
	[LightGBM] [Warning] bagging_freq is set=5, subsample_freq=1 will be ig

...

	[LightGBM] [Warning] min_data_in_leaf is set=6, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=6.
	[LightGBM] [Warning] num_threads is set=1, nthread=-1 will be ignored. Current value: num_threads=1.
	[LightGBM] [Warning] bagging_fraction is set=1.0, subsample=1.0 will be ignored. Current value: bagging_fraction=1.0.
	[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6.
	[LightGBM] [Warning] bagging_freq is set=2, subsample_freq=1 will be ignored. Current value: bagging_freq=2.
	[LightGBM] [Warning] min_data_in_leaf is set=6, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=6.
	[LightGBM] [Warning] num_threads is set=1, nthread=-1 will be ignored. Current value: num_threads=1.
	[LightGBM] [Warning] bagging_fraction is set=1.0, subsample=1.0 will be ignored. Current value: bagging_fraction=1.0.
	[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will b

	[LightGBM] [Warning] min_data_in_leaf is set=31, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=31.
	[LightGBM] [Warning] num_threads is set=1, nthread=-1 will be ignored. Current value: num_threads=1.
	[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8.
	[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9.
	[LightGBM] [Warning] bagging_freq is set=3, subsample_freq=1 will be ignored. Current value: bagging_freq=3.
	[LightGBM] [Warning] min_data_in_leaf is set=31, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=31.
	[LightGBM] [Warning] num_threads is set=1, nthread=-1 will be ignored. Current value: num_threads=1.
	[LightGBM] [Warning] bagging_fraction is set=0.9, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9.
	[LightGBM] [Warning] feature_fraction is set=0.7, colsample_bytree=1.0 wi

	[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8.
	[LightGBM] [Warning] feature_fraction is set=0.8, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8.
	[LightGBM] [Warning] bagging_freq is set=3, subsample_freq=1 will be ignored. Current value: bagging_freq=3.
	[LightGBM] [Warning] min_data_in_leaf is set=21, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=21.
	[LightGBM] [Warning] num_threads is set=1, nthread=-1 will be ignored. Current value: num_threads=1.
	[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8.
	[LightGBM] [Warning] feature_fraction is set=0.8, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8.
	[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=1 will be ignored. Current value: bagging_freq=1.
	[LightGBM] [Warning] min_data_in_leaf is set=31, min_child_samp

	[LightGBM] [Warning] num_threads is set=1, nthread=-1 will be ignored. Current value: num_threads=1.
	[LightGBM] [Warning] bagging_fraction is set=0.9, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9.
	[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6.
	[LightGBM] [Warning] bagging_freq is set=8, subsample_freq=1 will be ignored. Current value: bagging_freq=8.
	[LightGBM] [Warning] min_data_in_leaf is set=6, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=6.
	[LightGBM] [Warning] num_threads is set=1, nthread=-1 will be ignored. Current value: num_threads=1.
	[LightGBM] [Warning] bagging_fraction is set=0.9, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9.
	[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6.
	[LightGBM] [Warning] bagging_freq is set=8, subsample_freq=1 will be igno

	[LightGBM] [Warning] num_threads is set=1, nthread=-1 will be ignored. Current value: num_threads=1.
	[LightGBM] [Warning] bagging_fraction is set=0.6, subsample=1.0 will be ignored. Current value: bagging_fraction=0.6.
	[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9.
	[LightGBM] [Warning] bagging_freq is set=2, subsample_freq=1 will be ignored. Current value: bagging_freq=2.
	[LightGBM] [Warning] min_data_in_leaf is set=6, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=6.
	[LightGBM] [Warning] num_threads is set=1, nthread=-1 will be ignored. Current value: num_threads=1.
	[LightGBM] [Warning] bagging_fraction is set=0.6, subsample=1.0 will be ignored. Current value: bagging_fraction=0.6.
	[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9.
	[LightGBM] [Warning] bagging_freq is set=2, subsample_freq=1 will be igno

In [21]:
f1='%s/TCR_real_data/metabolomics/predictions_NoamMod/top20_nrandom20/results_df.pkl' %MyPath
results_df=pd.read_pickle(f1)
results_df.sort_values(by='pearson_r',ascending=False)


Size Coefficient_of_determination   pearson_r    pearson_p  \
100001806  247                    0.0178833    0.155483    0.0144407   
100001126  268                    0.0171648     0.13133    0.0316155   
100000008  270                    0.0154033    0.125274    0.0396838   
100015759  270                  -0.00691789   0.0656239     0.282614   
100003588  231                   -0.0147106   0.0651402     0.324269   
1504       270                  -0.00642318   0.0544944     0.372424   
100001395  270                  -0.00898665   0.0142527     0.815667   
100001777  270                  -0.00656531  0.00429222     0.944033   
X - 24549  270                  -0.00516168  -0.0107805     0.860039   
100008929  268                   -0.0075089  -0.0189357     0.757649   
100015966  270                   -0.0180592  -0.0338665     0.579537   
1094       270                   -0.0427834  -0.0428932     0.482766   
100001271  270                   -0.0416436  -0.0619991     0.310106   
100001322  179                   -0.0100377  -0.0806763     0.283018   
X - 24473  259                   -0.0151806    -0.10583    0.0891843   
100001409  270                   -0.0140055   -0.127322    0.0365342   
100020908  270                   -0.0241623   -0.138004     0.023331   
100001272  270                   -0.0171913    -0.15352    0.0115408   
100001263  270                    -0.013682   -0.163966   0.00693307   
X - 21411  266                   -0.0134436   -0.204104  0.000812568   

           spearman_r   spearman_p  
100001806    0.180436   0.00444429  
100001126    0.207617  0.000625517  
100000008    0.160923   0.00806693  
100015759    0.125085    0.0399864  
100003588    0.030832     0.641091  
1504        0.0691249     0.257667  
100001395  -0.0571738     0.349341  
100001777 -0.00643143     0.916225  
X - 24549 -0.00664451      0.91346  
100008929   -0.221035  0.000265533  
100015966  -0.0367602     0.547552  
1094       -0.0261317     0.669038  
100001271  -0.0418287     0.493706  
100001322   -0.109338     0.145126  
X - 24473   -0.107874    0.0831422  
100001409   -0.135343    0.0261596  
100020908   -0.126005     0.038535  
100001272    -0.15643    0.0100427  
100001263   -0.145182    0.0169781  
X - 21411   -0.216808  0.000368274

### using TCR sequences

In [ ]:
!python /home/sbenari/workspace/Microbiome/ShaniBA/RandomizedSearchCV_SHAP_LGBM_Shani.py /net/mraid08/export/\
genie/Lab/Personal/ShaniBAF/TCR_real_data/metabolomics/predictions_NoamMod/top20_bySeqs_nrandom20/ -path_to_X\
 /net/mraid08/export/genie/Lab/Personal/ShaniBAF/TCR_real_data/sharingAnalysis/sharingMatrix_PNP530_minNshared2_RA_onlyProductiveTrue__percShared5_OLtrimmed_binary\
 -path_to_Y /net/mraid08/export/genie/Lab/Personal/ShaniBAF/TCR_real_data/metabolomics/acs_top20_BD_PNP530.dat\
 -n_random 20

In [23]:
f1='%s/TCR_real_data/metabolomics/predictions_NoamMod/top20_bySeqs_nrandom20/results_df.pkl' %MyPath
results_df=pd.read_pickle(f1)
results_df.sort_values(by='pearson_r',ascending=False)


Size Coefficient_of_determination  pearson_r    pearson_p  \
100001777  270                    0.0356276   0.203962  0.000747871   
100001322  179                   0.00642244  0.0858936     0.252939   
100015966  270                  -0.00335432  0.0841626     0.167906   
100003588  231                   -0.0155503  0.0487083      0.46129   
1094       270                  -0.00795171  0.0463861     0.447808   
100001271  270                  7.05509e-05  0.0454214     0.457318   
100020908  270                   -0.0172872  0.0281564     0.645084   
100001126  268                   -0.0108014  0.0132527     0.829025   
1504       270                   -0.0157045 -0.0193874     0.751154   
100001272  270                  -0.00574098  -0.024041     0.694129   
100008929  268                   -0.0148422 -0.0272007     0.657553   
100000008  270                  -0.00809257 -0.0372363     0.542373   
X - 24549  270                  -0.00485274 -0.0550226       0.3678   
100001806  247                   -0.0465828 -0.0568843     0.373362   
X - 21411  266                     -0.04465 -0.0772514     0.209161   
100001263  270                   -0.0249865 -0.0835984     0.170785   
100015759  270                   -0.0192912  -0.120535    0.0478577   
100001395  270                  -0.00976721   -0.13974    0.0216307   
X - 24473  259                   -0.0227931  -0.181826   0.00331855   
100001409  270                   -0.0175649  -0.206934  0.000622507   

           spearman_r  spearman_p  
100001777    0.180174  0.00296662  
100001322   0.0531727    0.479617  
100015966   0.0685923    0.261361  
100003588   0.0324091    0.624111  
1094        0.0407547    0.504875  
100001271   0.0363242    0.552315  
100020908   0.0903402    0.138718  
100001126   0.0432817    0.480455  
1504       0.00860684    0.888051  
100001272  -0.0105343    0.863204  
100008929  -0.0553603    0.366662  
100000008  -0.0752597    0.217705  
X - 24549  -0.0850955    0.163226  
100001806  -0.0282861    0.658211  
X - 21411  -0.0763025    0.214826  
100001263  -0.0445543    0.465961  
100015759  -0.0830446    0.173646  
100001395    -0.16189  0.00768987  
X - 24473   -0.168389  0.00660212  
100001409    -0.12643   0.0378801

# use my old prediction mode to predict TMAO and top20 metabolites:

In [ ]:
#get metabolomics phenotype df:
TMAOf='/net/mraid08/export/genie/Lab/Personal/ShaniBAF/TCR_real_data/metabolomics/tmao_BD_PNP530.dat'
TMAO=pd.read_pickle(TMAOf)
top20f='/net/mraid08/export/genie/Lab/Personal/ShaniBAF/TCR_real_data/metabolomics/acs_top20_BD_PNP530.dat'
top20=pd.read_pickle(top20f)
metDF=pd.merge(TMAO,top20,how='inner', right_index=True,left_index=True)
print ('metDF shape is:', metDF.shape)

#new X: includes all TCR features, corrected for age and Gender
datasetFolder='%s/TCR_real_data/PNP530Combined' %MyPath
with open('/net/mraid08/export/genie/Lab/Personal/ShaniBAF/Sample files/BD lists/PNP530','rb') as fp:
    PNP530=pickle.load(fp)

f1='%s/TCR_real_data/Predictions/featureDFs/allTCRfeatures_percShared10__withRels_AgeGenderGFRCorr.dat' %MyPath
X_corrected=pd.read_pickle(f1).loc[PNP530,:]

resultFolder='%s/TCR_real_data/metabolomics/predictions_myOld' %MyPath
model=XGBRegressor
modelName='XGBRegressor'
featureSelectionMethod_list=['usingModel',None]         
k_list=[10,200]
task='reg'



for n,col in enumerate(metDF.columns):
    print col
    targetDF=binaryPhenDF[col]                     
 
    X=X_corrected.copy()
    Xname='X_AgeGenderGFRCorrected_withRels_PNP530'
    Y=targetDF
    Y=Y.dropna()
    X=X.loc[Y.index,:]

    max_depth_list=[3,6]
    learninglist=[(0.05,100)]
    gamma_list=[0,10]
    reg_lambda_list=[1]
    reg_alpha_list=[0]
    for learning in learninglist:
        learning_rate=learning[0]
        n_estimators=learning[1]
        
        
        for max_depth in max_depth_list:
            for gamma in gamma_list:
                for reg_alpha in reg_alpha_list:
                    for reg_lambda in reg_lambda_list:
            
                        model_params={'learning_rate': learning_rate, 'n_estimators': n_estimators,
                        'max_depth': max_depth,'num_threads':2,'bagging_fraction':0.5,'bagging_freq':1,
                        'bagging_seed':3,'gamma':gamma,'reg_alpha':reg_alpha,'reg_lambda':reg_lambda}


                        run_old_classification(X,Xname, Y, k_list,model, modelName,model_params,task,
                                           resultFolder,featureSelectionMethod_list)
    
